# Projet Mobility AMDM

In [2]:
import pandas as pd
import movingpandas as mpd
from datetime import timedelta

import hvplot.pandas  # Active l'extension hvplot pour pandas/geopandas
import holoviews as hv

# Active le moteur de rendu Bokeh (nécessaire pour l'interactif dans Jupyter)
hv.extension('bokeh')

/Users/ciscom/Desktop/Cours/M2/AMDM/projet/venv/lib/python3.13/site-packages/movingpandas/__init__.py:41: UserWarning: Missing optional dependencies. To use the trajectory smoother classes please install Stone Soup (see https://stonesoup.readthedocs.io/en/latest/#installation).
  warnings.warn(e.msg, UserWarning)


## chargement de la donnée

In [3]:
df_log= pd.read_csv("data/GPS_log.csv",sep=";")

In [5]:
df_log.head()

timestamp        lat       lon
0  2019-10-21 13:45:24+00  48.813044  2.148510
1  2019-10-21 13:45:40+00  48.813049  2.148507
2  2019-10-21 13:46:03+00  48.813049  2.148505
3  2019-10-21 13:46:28+00  48.813043  2.148513
4  2019-10-21 13:46:48+00  48.813049  2.148505

In [6]:
df_log.dtypes

timestamp        str
lat          float64
lon          float64
dtype: object

In [7]:
df_log['timestamp'] = pd.to_datetime(df_log['timestamp'])

In [8]:
df_log.dtypes

timestamp    datetime64[us, UTC]
lat                      float64
lon                      float64
dtype: object

In [9]:
#changement de l'index de dataframe
df_log = df_log.set_index('timestamp')

In [53]:
df_log.head()

lat       lon geometry
timestamp                                              
2019-10-21 13:45:24+00:00  48.813044  2.148510     None
2019-10-21 13:45:40+00:00  48.813049  2.148507     None
2019-10-21 13:46:03+00:00  48.813049  2.148505     None
2019-10-21 13:46:28+00:00  48.813043  2.148513     None
2019-10-21 13:46:48+00:00  48.813049  2.148505     None

In [11]:
track = mpd.Trajectory(df_log, traj_id=1, x='lon', y='lat')

/Users/ciscom/Desktop/Cours/M2/AMDM/projet/venv/lib/python3.13/site-packages/movingpandas/trajectory.py:158: TimeZoneWarning: Time zone information dropped from trajectory. All dates and times will use local time. This is applied by doing df.tz_localize(None). To use UTC or a different time zone, convert and drop time zone information prior to trajectory creation.
  warnings.warn(


In [12]:
print(f"Trajectoire complète : {track}")

Trajectoire complète : Trajectory 1 (2019-10-21 13:45:24 to 2019-10-28 12:31:02) | Size: 68808 | Length: 665972.4m
Bounds: (2.03762666666667, 48.7095233333333, 2.26096666666667, 48.8972016666667)
LINESTRING (2.1485104 48.8130436, 2.1485067 48.8130489, 2.1485049 48.813049, 2.1485134 48.8130434, 2


## Segmentation par de la trajectoire par jour

In [13]:
trj_day = mpd.TemporalSplitter(track).split(mode="day")

/Users/ciscom/Desktop/Cours/M2/AMDM/projet/venv/lib/python3.13/site-packages/movingpandas/trajectory_splitter.py:132: UserWarning: Temporal splitting results contain observation gaps that exceed your split size of D. Consider running the ObservationGapSplitter to further clean the results.
  warnings.warn(
/Users/ciscom/Desktop/Cours/M2/AMDM/projet/venv/lib/python3.13/site-packages/movingpandas/trajectory.py:186: MissingCRSWarning: Trajectory generated without CRS. Computations will use Euclidean distances.
  warnings.warn(
/Users/ciscom/Desktop/Cours/M2/AMDM/projet/venv/lib/python3.13/site-packages/movingpandas/trajectory.py:186: MissingCRSWarning: Trajectory generated without CRS. Computations will use Euclidean distances.
  warnings.warn(
/Users/ciscom/Desktop/Cours/M2/AMDM/projet/venv/lib/python3.13/site-packages/movingpandas/trajectory.py:186: MissingCRSWarning: Trajectory generated without CRS. Computations will use Euclidean distances.
  warnings.warn(
/Users/ciscom/Desktop/Cour

In [14]:
print(f"Nombre de trajectoires : {len(trj_day)}")

Nombre de trajectoires : 7


In [15]:
# 4. Vérification rapide
for traj in trj_day:
    print(f"Jour : {traj.get_start_time().date()} | Points : {len(traj.df)}")

Jour : 2019-10-21 | Points : 8160
Jour : 2019-10-22 | Points : 18974
Jour : 2019-10-23 | Points : 20352
Jour : 2019-10-24 | Points : 5771
Jour : 2019-10-25 | Points : 5826
Jour : 2019-10-26 | Points : 3418
Jour : 2019-10-28 | Points : 6313


In [ ]:
# ajout de la vitesse au traj

In [16]:
trj_day.add_speed(overwrite=True)

TrajectoryCollection with 7 trajectories

In [52]:
print(trj_day.trajectories[0].df.head())

                                     geometry traj_id         speed  \
timestamp                                                             
2019-10-21 13:45:24  POINT (2.14851 48.81304)     1_0  4.039841e-07   
2019-10-21 13:45:40  POINT (2.14851 48.81305)     1_0  4.039841e-07   
2019-10-21 13:46:03   POINT (2.1485 48.81305)     1_0  7.838155e-08   
2019-10-21 13:46:28  POINT (2.14851 48.81304)     1_0  4.071560e-07   
2019-10-21 13:46:48   POINT (2.1485 48.81305)     1_0  5.158730e-07   

                               datetime  
timestamp                                
2019-10-21 13:45:24 2019-10-21 13:45:24  
2019-10-21 13:45:40 2019-10-21 13:45:40  
2019-10-21 13:46:03 2019-10-21 13:46:03  
2019-10-21 13:46:28 2019-10-21 13:46:28  
2019-10-21 13:46:48 2019-10-21 13:46:48  


## Visualisation des trajectoires journalieres

In [18]:
# On parcourt chaque trajectoire (chaque jour) dans la collection
for traj in trj_day:
    # On accède au DataFrame de ce jour spécifique et on crée la colonne
    traj.df['datetime'] = traj.df.index

# Vérification : on regarde le premier jour pour voir si la colonne est là
print(trj_day.trajectories[0].df.head())

                                     geometry traj_id         speed  \
timestamp                                                             
2019-10-21 13:45:24  POINT (2.14851 48.81304)     1_0  4.039841e-07   
2019-10-21 13:45:40  POINT (2.14851 48.81305)     1_0  4.039841e-07   
2019-10-21 13:46:03   POINT (2.1485 48.81305)     1_0  7.838155e-08   
2019-10-21 13:46:28  POINT (2.14851 48.81304)     1_0  4.071560e-07   
2019-10-21 13:46:48   POINT (2.1485 48.81305)     1_0  5.158730e-07   

                               datetime  
timestamp                                
2019-10-21 13:45:24 2019-10-21 13:45:24  
2019-10-21 13:45:40 2019-10-21 13:45:40  
2019-10-21 13:46:03 2019-10-21 13:46:03  
2019-10-21 13:46:28 2019-10-21 13:46:28  
2019-10-21 13:46:48 2019-10-21 13:46:48  


In [22]:
# 1. Préparation (comme avant)
gdf_trajs = trj_day.to_traj_gdf()

# On recrée la colonne date pour la légende
gdf_trajs['start_time'] = [traj.get_start_time() for traj in trj_day]
gdf_trajs['date_str'] = gdf_trajs['start_time'].dt.strftime('%Y-%m-%d')

# 2. Visualisation Interactive avec .explore()
# Pas besoin de convertir en WebMercator (EPSG:3857), explore gère ça tout seul.
m = gdf_trajs.explore(
    column='date_str',     # La colonne pour colorer et créer la légende
    cmap='Set1',           # Palette de couleurs vives
    tiles='CartoDB positron', # Fond de carte (aussi dispo: 'OpenStreetMap', 'CartoDB dark_matter')
    style_kwds={'weight': 5}, # Épaisseur du trait
    legend=True,           # Afficher la légende
    tooltip=['date_str', 'traj_id'], # Ce qui s'affiche quand on passe la souris dessus
    popup=True             # Ce qui s'affiche quand on clique
)

# 3. Afficher la carte dans le notebook
m

## Le netoyage des trajectoires

In [28]:
cleaner = mpd.OutlierCleaner(trj_day)
cleaned_trajs = cleaner.clean(v_max=45, alpha=0.5)

print(f"Trajectoires après nettoyage des sauts : {len(cleaned_trajs)}")

/Users/ciscom/Desktop/Cours/M2/AMDM/projet/venv/lib/python3.13/site-packages/movingpandas/trajectory.py:186: MissingCRSWarning: Trajectory generated without CRS. Computations will use Euclidean distances.
  warnings.warn(
/Users/ciscom/Desktop/Cours/M2/AMDM/projet/venv/lib/python3.13/site-packages/movingpandas/trajectory.py:186: MissingCRSWarning: Trajectory generated without CRS. Computations will use Euclidean distances.
  warnings.warn(
/Users/ciscom/Desktop/Cours/M2/AMDM/projet/venv/lib/python3.13/site-packages/movingpandas/trajectory.py:186: MissingCRSWarning: Trajectory generated without CRS. Computations will use Euclidean distances.
  warnings.warn(
/Users/ciscom/Desktop/Cours/M2/AMDM/projet/venv/lib/python3.13/site-packages/movingpandas/trajectory.py:186: MissingCRSWarning: Trajectory generated without CRS. Computations will use Euclidean distances.
  warnings.warn(
/Users/ciscom/Desktop/Cours/M2/AMDM/projet/venv/lib/python3.13/site-packages/movingpandas/trajectory.py:186: Mis

Trajectoires après nettoyage des sauts : 7


## Les points d'arrets

In [29]:
# 1. Compter le nombre total de points AVANT
total_points_avant = sum([len(traj.df) for traj in trj_day])

# 2. Compter le nombre total de points APRÈS
total_points_apres = sum([len(traj.df) for traj in cleaned_trajs])

# 3. Calcul des différences
points_supprimes = total_points_avant - total_points_apres
pourcentage = (points_supprimes / total_points_avant) * 100

print(f"--- Bilan du Nettoyage (Outliers) ---")
print(f"Points total avant : {total_points_avant}")
print(f"Points total après : {total_points_apres}")
print(f"Points supprimés   : {points_supprimes}")
print(f"Pourcentage de réduction : {pourcentage:.2f}%")

--- Bilan du Nettoyage (Outliers) ---
Points total avant : 68814
Points total après : 68811
Points supprimés   : 3
Pourcentage de réduction : 0.00%


In [ ]:
from movingpandas import TrajectoryStopDetector
from datetime import timedelta

# 1. Initialiser le détecteur sur vos données (trj_day ou cleaned_trajs)
detector = TrajectoryStopDetector(cleaned_trajs)

# 2. Lancer la détection
# min_duration : Durée minimale pour considérer un arrêt (ex: 300 secondes = 5 min)
# max_diameter : Rayon du cercle dans lequel on doit rester (ex: 100 mètres)
stop_points = detector.get_stop_points(min_duration=timedelta(seconds=300), 
                                       max_diameter=200)

print(f"Nombre d'arrêts détectés : {len(stop_points)}")

# 3. Afficher les détails (Heure début, fin, durée)
# C'est très utile pour votre rapport !
print(stop_points[['start_time', 'end_time', 'duration_s']].head())

/Users/ciscom/Desktop/Cours/M2/AMDM/projet/venv/lib/python3.13/site-packages/shapely/constructive.py:1353: RuntimeWarning: invalid value encountered in oriented_envelope
  return lib.oriented_envelope(geometry, **kwargs)
/Users/ciscom/Desktop/Cours/M2/AMDM/projet/venv/lib/python3.13/site-packages/shapely/constructive.py:1353: RuntimeWarning: invalid value encountered in oriented_envelope
  return lib.oriented_envelope(geometry, **kwargs)
/Users/ciscom/Desktop/Cours/M2/AMDM/projet/venv/lib/python3.13/site-packages/shapely/constructive.py:1353: RuntimeWarning: invalid value encountered in oriented_envelope
  return lib.oriented_envelope(geometry, **kwargs)
/Users/ciscom/Desktop/Cours/M2/AMDM/projet/venv/lib/python3.13/site-packages/shapely/constructive.py:1353: RuntimeWarning: invalid value encountered in oriented_envelope
  return lib.oriented_envelope(geometry, **kwargs)
/Users/ciscom/Desktop/Cours/M2/AMDM/projet/venv/lib/python3.13/site-packages/shapely/constructive.py:1353: RuntimeWa

Nombre d'arrêts détectés : 21
                                 start_time            end_time  duration_s
stop_id                                                                    
1_0_2019-10-21 13:45:24 2019-10-21 13:45:24 2019-10-22 00:00:01     36877.0
1_1_2019-10-22 00:00:01 2019-10-22 00:00:01 2019-10-23 00:00:18     86417.0
1_2_2019-10-23 00:00:18 2019-10-23 00:00:18 2019-10-24 00:00:32     86414.0
1_3_2019-10-24 00:00:32 2019-10-24 00:00:32 2019-10-25 07:05:00    111868.0
1_4_2019-10-25 07:05:00 2019-10-25 07:05:00 2019-10-26 11:28:10    102190.0


/Users/ciscom/Desktop/Cours/M2/AMDM/projet/venv/lib/python3.13/site-packages/movingpandas/trajectory.py:186: MissingCRSWarning: Trajectory generated without CRS. Computations will use Euclidean distances.
  warnings.warn(
/Users/ciscom/Desktop/Cours/M2/AMDM/projet/venv/lib/python3.13/site-packages/movingpandas/trajectory.py:186: MissingCRSWarning: Trajectory generated without CRS. Computations will use Euclidean distances.
  warnings.warn(
/Users/ciscom/Desktop/Cours/M2/AMDM/projet/venv/lib/python3.13/site-packages/movingpandas/trajectory.py:186: MissingCRSWarning: Trajectory generated without CRS. Computations will use Euclidean distances.
  warnings.warn(
/Users/ciscom/Desktop/Cours/M2/AMDM/projet/venv/lib/python3.13/site-packages/movingpandas/trajectory.py:186: MissingCRSWarning: Trajectory generated without CRS. Computations will use Euclidean distances.
  warnings.warn(
/Users/ciscom/Desktop/Cours/M2/AMDM/projet/venv/lib/python3.13/site-packages/movingpandas/trajectory.py:186: Mis

## Les Segments d'arrets

## Visualisation 

In [35]:
# 2. Préparation des colonnes pour la visualisation
# On crée 'date_str' pour la légende (Couleur par jour)
stop_points['date_str'] = stop_points['start_time'].dt.strftime('%Y-%m-%d')

# On crée une durée lisible en minutes pour le popup
stop_points['duration_min'] = (stop_points['duration_s'] / 60).round(1)

# On convertit les timestamps en str pour éviter les bugs d'affichage Folium parfois
stop_points['start_str'] = stop_points['start_time'].astype(str)
stop_points['end_str'] = stop_points['end_time'].astype(str)

print(f"{len(stop_points)} arrêts détectés.")

21 arrêts détectés.


In [ ]:
stop_points[['traj_id','date_str','start_time','end_time','duration_min','geometry']].head()

geometry          start_time  \
stop_id                                                                 
1_0_2019-10-21 13:45:24  POINT (2.14863 48.81315) 2019-10-21 13:45:24   
1_1_2019-10-22 00:00:01  POINT (2.14865 48.81322) 2019-10-22 00:00:01   
1_2_2019-10-23 00:00:18  POINT (2.14862 48.81316) 2019-10-23 00:00:18   
1_3_2019-10-24 00:00:32  POINT (2.14862 48.81312) 2019-10-24 00:00:32   
1_4_2019-10-25 07:05:00  POINT (2.15254 48.76309) 2019-10-25 07:05:00   

                                   end_time traj_id  duration_s    date_str  \
stop_id                                                                       
1_0_2019-10-21 13:45:24 2019-10-22 00:00:01     1_0     36877.0  2019-10-21   
1_1_2019-10-22 00:00:01 2019-10-23 00:00:18     1_1     86417.0  2019-10-22   
1_2_2019-10-23 00:00:18 2019-10-24 00:00:32     1_2     86414.0  2019-10-23   
1_3_2019-10-24 00:00:32 2019-10-25 07:05:00     1_3    111868.0  2019-10-24   
1_4_2019-10-25 07:05:00 2019-10-26 11:28:10     1_4    102190.0  2019-10-25   

                         duration_min            start_str  \
stop_id                                                      
1_0_2019-10-21 13:45:24         614.6  2019-10-21 13:45:24   
1_1_2019-10-22 00:00:01        1440.3  2019-10-22 00:00:01   
1_2_2019-10-23 00:00:18        1440.2  2019-10-23 00:00:18   
1_3_2019-10-24 00:00:32        1864.5  2019-10-24 00:00:32   
1_4_2019-10-25 07:05:00        1703.2  2019-10-25 07:05:00   

                                     end_str  
stop_id                                       
1_0_2019-10-21 13:45:24  2019-10-22 00:00:01  
1_1_2019-10-22 00:00:01  2019-10-23 00:00:18  
1_2_2019-10-23 00:00:18  2019-10-24 00:00:32  
1_3_2019-10-24 00:00:32  2019-10-25 07:05:00  
1_4_2019-10-25 07:05:00  2019-10-26 11:28:10

In [50]:
import folium
import geopandas as gpd

# --- PARTIE 1 : Préparation des Trajectoires (Lignes) ---
gdf_traj = trj_day.to_traj_gdf()

# CORRECTION : On récupère manuellement l'heure de début pour chaque ligne
gdf_traj['start_time'] = [traj.get_start_time() for traj in trj_day]

# On crée la colonne texte pour la légende
gdf_traj['date_str'] = gdf_traj['start_time'].dt.strftime('%Y-%m-%d')


# --- PARTIE 2 : Préparation des Arrêts (Points) ---
# On s'assure que stop_points a bien les bonnes colonnes (au cas où)
if 'date_str' not in stop_points.columns:
    stop_points['date_str'] = stop_points['start_time'].dt.strftime('%Y-%m-%d')
    stop_points['duration_min'] = (stop_points['duration_s'] / 60).round(1)
    stop_points['start_str'] = stop_points['start_time'].astype(str)
    stop_points['end_str'] = stop_points['end_time'].astype(str)


# --- PARTIE 3 : Visualisation Superposée ---

# 1. D'abord les Trajets (Lignes)
m = gdf_traj.explore(
    column='date_str',   # Colorer par jour
    cmap='Pastel1',      # Couleurs douces
    tiles='CartoDB positron',
    style_kwds={'weight': 3, 'opacity': 0.6},
    name="Trajets"       # Nom de la couche
)

# 2. Ensuite les Arrêts (Points), ajoutés sur la carte 'm'
stop_points.explore(
    m=m,                 # <--- IMPORTANT : On ajoute sur la carte précédente
    column='date_str',   # Même couleur que le jour
    cmap='Set1',         # Couleurs vives
    marker_type='circle_marker',
    marker_kwds={'radius': 8, 'fill': True, 'fill_opacity': 1},
    style_kwds={'color': 'black', 'weight': 1}, # Contour noir pour bien les voir
    tooltip=['date_str', 'duration_min'],
    popup=['start_str', 'end_str', 'duration_min'],
    name="Arrêts"        # Nom de la couche
)

# 3. Ajouter le contrôleur de couches (pour cocher/décocher)
folium.LayerControl().add_to(m)

# 4. Afficher
m

In [42]:
print(f"{len(stop_points)} arrêts détectés.")

21 arrêts détectés.
